In [81]:
import pandas as pd
import numpy as np
import psycopg2
import matplotlib.pyplot as plt
import seaborn as sns
from psycopg2 import sql
from sqlalchemy import create_engine

from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler, normalize
import plotly.io as pio
import plotly.express as px

In [63]:
#Load Clean Df from DB
connection_params = {
  "host": "localhost",
  "user": "postgres",
  "password": "post33##",
  "port": "5432"
}
db_name = 'telecom'
connection_params["database"] = db_name
engine = create_engine(f"postgresql+psycopg2://{connection_params['user']}:{connection_params['password']}@{connection_params['host']}:{connection_params['port']}/{connection_params['database']}")
db_conn = engine.connect()
df = pd.read_sql("select * from \"clean_df\"", db_conn);
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 146891 entries, 0 to 146890
Data columns (total 53 columns):
 #   Column                          Non-Null Count   Dtype  
---  ------                          --------------   -----  
 0   index                           146891 non-null  int64  
 1   Bearer Id                       146891 non-null  int64  
 2   Start                           146891 non-null  object 
 3   Start ms                        146891 non-null  float64
 4   End                             146891 non-null  object 
 5   End ms                          146891 non-null  float64
 6   IMSI                            146891 non-null  float64
 7   MSISDN/Number                   146891 non-null  int64  
 8   IMEI                            146891 non-null  float64
 9   Last Location Name              146891 non-null  object 
 10  Avg RTT DL (ms)                 146891 non-null  float64
 11  Avg RTT UL (ms)                 146891 non-null  float64
 12  Avg Bearer TP DL

In [64]:
user_engagement_df = df[['MSISDN/Number', 'Bearer Id', 'Dur (ms)', 'Data_Volume_Total (Bytes)']]
user_engagement_df

MSISDN/Number            Bearer Id      Dur (ms)  \
0         33664962239 -9223372036854775808  2.450964e+08   
1         33681854413 -9223372036854775808  2.450964e+08   
2         33760627129 -9223372036854775808  2.450964e+08   
3         33750343200 -9223372036854775808  2.450964e+08   
4         33699795932 -9223372036854775808  2.450964e+08   
...               ...                  ...           ...   
146886    33645655643 -9223372036854775808  1.135452e+08   
146887    33668648496 -9223372036854775808  5.958779e+07   
146888    33650688697  7277825670196679680  8.123076e+07   
146889    33663449963  7349883264234609664  9.797070e+07   
146890    33619622058 -9223372036854775808  9.791063e+07   

        Data_Volume_Total (Bytes)  
0                     345629377.0  
1                     707185356.0  
2                     307690973.0  
3                     889352748.0  
4                     607681403.0  
...                           ...  
146886                922173944.0  
146887                872761860.0  
146888                631804110.0  
146889                705783925.0  
146890                401522016.0  

[146891 rows x 4 columns]

In [65]:
user_engagement_df = user_engagement_df.groupby(
    'MSISDN/Number').agg({'Bearer Id': 'count', 'Dur (ms)': 'sum', 'Data_Volume_Total (Bytes)': 'sum'})
user_engagement_df = user_engagement_df.rename(
    columns={'Bearer Id': 'xDR Sessions'})
user_engagement_df.head()


xDR Sessions     Dur (ms)  Data_Volume_Total (Bytes)
MSISDN/Number                                                      
33601001722               1  116720140.0               8.786906e+08
33601001754               1  181230963.0               1.568596e+08
33601002511               1  134969374.0               5.959665e+08
33601007832               1   49878024.0               4.223207e+08
33601008617               2   37104453.0               1.457411e+09

# Top 10 Customers per xDR Sessions

In [66]:
user_engagement_df.nlargest(10, 'xDR Sessions')

xDR Sessions      Dur (ms)  Data_Volume_Total (Bytes)
MSISDN/Number                                                       
33626320676              18  4.007185e+09               7.971167e+09
33614892860              17  3.900162e+09               8.846226e+09
33625779332              17  4.138211e+09               8.499621e+09
33659725664              16  3.492455e+09               7.705863e+09
33675877202              15  3.332109e+09               7.891111e+09
33760536639              15  3.396757e+09               8.514774e+09
33667163239              13  3.114072e+09               5.618394e+09
33603127838              12  2.855408e+09               4.976195e+09
33604515716              12  2.780008e+09               5.487855e+09
33627080969              12  2.782315e+09               5.754731e+09

# Top 10 Customers per Duration (ms)

In [67]:
user_engagement_df.nlargest(10, 'Dur (ms)')

xDR Sessions      Dur (ms)  Data_Volume_Total (Bytes)
MSISDN/Number                                                       
33625779332              17  4.138211e+09               8.499621e+09
33626320676              18  4.007185e+09               7.971167e+09
33614892860              17  3.900162e+09               8.846226e+09
33659725664              16  3.492455e+09               7.705863e+09
33760536639              15  3.396757e+09               8.514774e+09
33675877202              15  3.332109e+09               7.891111e+09
33667163239              13  3.114072e+09               5.618394e+09
33603127838              12  2.855408e+09               4.976195e+09
33627080969              12  2.782315e+09               5.754731e+09
33604515716              12  2.780008e+09               5.487855e+09

# Top 10 Customers per Total Data Volume (ms)

In [68]:
user_engagement_df.nlargest(10, 'Data_Volume_Total (Bytes)')

xDR Sessions      Dur (ms)  Data_Volume_Total (Bytes)
MSISDN/Number                                                       
33614892860              17  3.900162e+09               8.846226e+09
33760536639              15  3.396757e+09               8.514774e+09
33625779332              17  4.138211e+09               8.499621e+09
33626320676              18  4.007185e+09               7.971167e+09
33675877202              15  3.332109e+09               7.891111e+09
33659725664              16  3.492455e+09               7.705863e+09
33666464084              11  2.596981e+09               7.308501e+09
33760413819              12  2.676757e+09               7.132371e+09
33664712899              11  2.603487e+09               6.872337e+09
33698792269              11  2.639278e+09               6.540899e+09

In [69]:
user_engagement_df.boxplot();

In [70]:
def replace_outliers_with_fences(df,columns):
    for col in columns:
        Q1, Q3 = df[col].quantile(0.25), df[col].quantile(0.75)
        IQR = Q3 - Q1
        cut_off = IQR * 1.5
        lower, upper = Q1 - cut_off, Q3 + cut_off

        df[col] = np.where(df[col] > upper, upper, df[col])
        df[col] = np.where(df[col] < lower, lower, df[col])
    return df

In [71]:
user_engagement_df = replace_outliers_with_fences(user_engagement_df,['xDR Sessions', 'Dur (ms)', 'Data_Volume_Total (Bytes)'])

In [73]:
user_engagement_df.boxplot()

<Axes: >

# K-means  Clustering

In [75]:
scaler_instance = StandardScaler()
scaled_data = scaler_instance.fit_transform(user_engagement_df)
scaled_data

array([[-0.54866448, -0.14577497,  0.54827045],
       [-0.54866448,  0.61463413, -1.28049501],
       [-0.54866448,  0.06933442, -0.1680137 ],
       ...,
       [-0.54866448, -1.41773719,  0.13265093],
       [-0.54866448,  0.1402856 , -0.46103724],
       [-0.54866448,  1.36743628, -0.16719958]])

# Normalize Df

In [76]:
normalized_data = normalize(scaled_data)
normalized_data

array([[-0.69518984, -0.18470538,  0.69469058],
       [-0.3603343 ,  0.40365974, -0.84096255],
       [-0.94926842,  0.11995851, -0.29068785],
       ...,
       [-0.35954949, -0.92906814,  0.08692849],
       [-0.75133573,  0.19210571, -0.63133985],
       [-0.37000452,  0.92216213, -0.11275488]])

In [77]:
kmeans = KMeans(n_clusters=3, random_state=1).fit(normalized_data)
kmeans.labels_

C:\Users\Fandingo\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


array([1, 0, 0, ..., 1, 0, 0])

In [79]:
user_engagement_df.insert(0, 'cluster', kmeans.labels_)
user_engagement_df

cluster  xDR Sessions      Dur (ms)  \
MSISDN/Number                                          
33601001722            1           1.0  1.167201e+08   
33601001754            0           1.0  1.812310e+08   
33601002511            0           1.0  1.349694e+08   
33601007832            1           1.0  4.987802e+07   
33601008617            2           2.0  3.710445e+07   
...                  ...           ...           ...   
33789967113            0           1.0  1.604616e+08   
33789980299            2           2.0  2.103901e+08   
33789996170            1           1.0  8.810688e+06   
33789997247            0           1.0  1.409887e+08   
337000037000919        0           1.0  2.450964e+08   

                 Data_Volume_Total (Bytes)  
MSISDN/Number                               
33601001722                   8.786906e+08  
33601001754                   1.568596e+08  
33601002511                   5.959665e+08  
33601007832                   4.223207e+08  
33601008617                   1.457411e+09  
...                                    ...  
33789967113                   2.081231e+08  
33789980299                   1.094693e+09  
33789996170                   7.146416e+08  
33789997247                   4.803073e+08  
337000037000919               5.962878e+08  

[105719 rows x 4 columns]

In [80]:
user_engagement_df['cluster'].value_counts()

cluster
1    52859
2    28336
0    24524
Name: count, dtype: int64

In [82]:
pio.renderers.default = "notebook"
fig = px.scatter(user_engagement_df, x='Data_Volume_Total (Bytes)', y='Dur (ms)',
                 color='cluster', size='xDR Sessions')
fig.show()

In [86]:
sns.pairplot(
    user_engagement_df[['cluster','xDR Sessions', 'Dur (ms)', 'Data_Volume_Total (Bytes)']],
     hue = 'cluster', diag_kind = 'kde',
             plot_kws = {'alpha': 0.6, 's': 80, 'edgecolor': 'k'},
             height=3
);

C:\Users\Fandingo\anaconda3\Lib\site-packages\seaborn\axisgrid.py:118: UserWarning:

The figure layout has changed to tight



In [92]:
cluster0 = user_engagement_df[user_engagement_df["cluster"]==0]
cluster0[['xDR Sessions', 'Dur (ms)', 'Data_Volume_Total (Bytes)']].describe()

xDR Sessions      Dur (ms)  Data_Volume_Total (Bytes)
count  24524.000000  2.452400e+04               2.452400e+04
mean       1.000571  1.720445e+08               4.890684e+08
std        0.023887  3.883267e+07               2.452094e+08
min        1.000000  1.155029e+08               3.357584e+07
25%        1.000000  1.410469e+08               2.771558e+08
50%        1.000000  1.625150e+08               4.856968e+08
75%        1.000000  1.909921e+08               7.012200e+08
max        2.000000  3.229058e+08               9.507607e+08

In [91]:
cluster0 = user_engagement_df[user_engagement_df["cluster"]==1]
cluster0[['xDR Sessions', 'Dur (ms)', 'Data_Volume_Total (Bytes)']].describe()

xDR Sessions      Dur (ms)  Data_Volume_Total (Bytes)
count  52859.000000  5.285900e+04               5.285900e+04
mean       1.006186  6.694024e+07               5.000288e+08
std        0.078410  3.139293e+07               2.431851e+08
min        1.000000  7.142988e+06               3.324901e+07
25%        1.000000  3.517672e+07               2.918199e+08
50%        1.000000  8.431951e+07               5.027718e+08
75%        1.000000  8.640129e+07               7.096547e+08
max        2.000000  1.250431e+08               9.495983e+08

In [93]:
cluster0 = user_engagement_df[user_engagement_df["cluster"]==2]
cluster0[['xDR Sessions', 'Dur (ms)', 'Data_Volume_Total (Bytes)']].describe()

xDR Sessions      Dur (ms)  Data_Volume_Total (Bytes)
count  28336.000000  2.833600e+04               2.833600e+04
mean       2.318535  2.078403e+08               1.114870e+09
std        0.547993  9.330321e+07               3.728221e+08
min        2.000000  1.823580e+07               1.197685e+08
25%        2.000000  1.314686e+08               8.341170e+08
50%        2.000000  2.001904e+08               1.115346e+09
75%        3.000000  3.180281e+08               1.466224e+09
max        3.500000  3.229058e+08               1.604259e+09

# Total Traffic of Each Application Per User

In [95]:
user_engagement_df = df[['MSISDN/Number', 'Data_Volume_Gaming (Bytes)', 'Data_Volume_Social (Bytes)',
    'Data_Volume_Google (Bytes)', 'Data_Volume_Email (Bytes)', 'Data_Volume_Youtube (Bytes)',
    'Data_Volume_Netflix (Bytes)', 'Data_Volume_Other (Bytes)']]

In [97]:
user_engagement_df = user_engagement_df.groupby(
    'MSISDN/Number').sum()
user_engagement_df.head()

Data_Volume_Gaming (Bytes)  Data_Volume_Social (Bytes)  \
MSISDN/Number                                                           
33601001722                  8.124587e+08                   2232135.0   
33601001754                  1.197501e+08                   2660565.0   
33601002511                  5.388277e+08                   3195623.0   
33601007832                  3.911261e+08                    280294.0   
33601008617                  1.314798e+09                   2912542.0   

               Data_Volume_Google (Bytes)  Data_Volume_Email (Bytes)  \
MSISDN/Number                                                          
33601001722                     4389005.0                  1331362.0   
33601001754                     5334863.0                  3307781.0   
33601002511                     3443126.0                  3205380.0   
33601007832                     9678493.0                  2284670.0   
33601008617                    18499616.0                  3305469.0   

               Data_Volume_Youtube (Bytes)  Data_Volume_Netflix (Bytes)  \
MSISDN/Number                                                             
33601001722                     21624548.0                   27180981.0   
33601001754                     12432223.0                   11221763.0   
33601002511                     21333570.0                   19353900.0   
33601007832                      6977321.0                    1942092.0   
33601008617                     41533002.0                   49201724.0   

               Data_Volume_Other (Bytes)  
MSISDN/Number                             
33601001722                  386570872.0  
33601001754                  281710071.0  
33601002511                  501693672.0  
33601007832                   35279702.0  
33601008617                  804804484.0

# Top 10 Engaged Users Per App

In [99]:
gaming = user_engagement_df.nlargest(10, "Data_Volume_Gaming (Bytes)")['Data_Volume_Gaming (Bytes)']
social_media = user_engagement_df.nlargest(10, "Data_Volume_Social (Bytes)")['Data_Volume_Social (Bytes)']
google = user_engagement_df.nlargest(10, "Data_Volume_Google (Bytes)")['Data_Volume_Google (Bytes)']
email = user_engagement_df.nlargest(10, "Data_Volume_Email (Bytes)")['Data_Volume_Email (Bytes)']
youtube = user_engagement_df.nlargest(10, "Data_Volume_Youtube (Bytes)")['Data_Volume_Youtube (Bytes)']
social_media = user_engagement_df.nlargest(10, "Data_Volume_Netflix (Bytes)")['Data_Volume_Netflix (Bytes)']
other = user_engagement_df.nlargest(10, "Data_Volume_Other (Bytes)")['Data_Volume_Other (Bytes)']

NameError: name 'df_telco_user_app_engagement_df' is not defined